# Simulating Glycan Shielding

Proteins that are glycosylated have parts of their surface covered by the attached glycan chains. This makes them inaccessible for certain interactions such as with antibodies. To ascertain the "shielding effect" of glycans on a protein surface one can use molecular dynamics to obtain high quality conformers, albeit at a high computational cost. 

Glycosylator offers a simple quick-simulation tool to sample glycan conformations on a glycosylated scaffold without the need for extensive computational resources. To that end Glycosylator provides the `GlycoShield` class and the top-level `quickshield` function. These will generate a dataframe containing an "exposure score" for each residue in the scaffold, which is a measure of how much a residue is "covered" by glycan chains and thus not exposed to the environment. Lower values indicate higher coverage by glycans and vice versa.

In [1]:
import glycosylator as gl
gl.visual.set_backend("py3dmol")

### Using `quickshield`

The most convenient way to simulate shielding is the `quickshield` function. It accepts a glycosylated `Scaffold` object as input and returns a `GlycoShield` which contains the data we are interested in. Let's see how:

In [2]:
# first load a scaffold
protein = gl.Protein.load("./files/protein_optimized.pkl")
for i, glycan in enumerate(protein.glycans):
    glycan.id = f"glycan-{i}"
protein.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [3]:
# now run the quickshield
shield = gl.quickshield(protein)

We can now inspect the exposure data by plotting it using plotly or matplotlib like so:

In [4]:
shield.exposure.plotly().show()

/Users/noahhk/anaconda3/envs/glyco2/lib/python3.11/site-packages/plotly/express/_core.py:1985: FutureWarning: When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.
  sf: grouped.get_group(s if len(s) > 1 else s[0])


We can actually visualize the "exposure" of the scaffold residues also as a heat map in the Py3DMol visualization like so:

In [5]:
# show the results
shield.py3dmol().show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

And to obtain the actual data we can use the `df` attribute:

In [6]:
shield.exposure.df

chain resname  serial     exposure
0       A     ALA       1   710.595306
1       A     LEU     246  1361.795249
2       B     ALA     460   529.003276
3       A     THR     124  1983.636554
4       A     ILE     370  1496.034150
..    ...     ...     ...          ...
573     A     ASN     122  1528.972768
574     A     ILE     245  2144.561491
575     A     MET     123  1719.207949
576     B     GLY     459   645.095968
577     A     GLN     369   915.990524

[578 rows x 4 columns]

## Using the `GlycoShield` directly

The `quickshield` function is, well, quick... but it lacks some customizability. Let's say we want to sample more edges for each glycan (the default is 3 edges per simulation) we will need to use the `GlycoShield` class directly. We can set it up by simply passing the scaffold to it as only argument and then use its `simulate` method to perform the shielding simulation like so:

In [7]:
# setup the shield simulator
shield = gl.GlycoShield(protein)

# now run the simulation
out = shield.simulate(angle_step=50, repeats=3, edge_samples=5, save_conformations_to="./files/glycoshield", visualize_conformations=False)

When providing `visualize_conformations=True` then `out` will be a tuple of the dataframe and a `Py3DmolViewer`. The visuals of the sampled (and accepted; ones with clashes are ignored) conformations are also stored by the GlycoShield so when we call `py3dmol` we can create a "full" view with the heatmap and conformations using:

```python
shield.py3dmol().show()
```

Keep in mind though that depending on the size of the system this can be very, very, very..... memory intensive and thus slow down the code. It is usually better (and more likely useful anyway) to save the conformations into PDB files and then visualize them externally.  

Anyways, this is what the glycoshield looks like when we assemble the exported PDB files:

![](../_static/_resources/glycoshield.gif)

And with that we have reached the end of this tutorial. We have seen how we can use the `GlycoShield` class to perform sampling of glycan conformations on a scaffold such as a protein and obtain data on how covered or exposed certain residues are. Thanks for checking out this tutorial and good luck in your project using Glycosylator!